# Alternative Fuels Stations Analysis

## Objectives
- Analysis valid for current situation (October 2022)
- Visualization of the current trends
- Visualization of the current state of stations evolution
- [Optional] Visualization of evolution of charging infrustructure
- [Optional] Visualization of correlations with incentives

## Dataset Light Duty Vehilces In USA
- Last update 26/10/2022
- Source: https://afdc.energy.gov/data_download

In [54]:
import numpy as np
np.set_printoptions(precision=2)
import plotly.express as px
import plotly.graph_objs as go
import pandas as pd

# read csv
vehicles=pd.read_csv("Data/26:10:2022/light-duty-vehicles.csv", keep_default_na=False)
print(f"Number of Columns: {len(vehicles.columns)} \n")
print("\n".join(vehicles.columns))

Number of Columns: 38 

Vehicle ID
Fuel ID
Fuel Configuration ID
Manufacturer ID
Category ID
Model
Model Year
Alternative Fuel Economy City
Alternative Fuel Economy Highway
Alternative Fuel Economy Combined
Conventional Fuel Economy City
Conventional Fuel Economy Highway
Conventional Fuel Economy Combined
Transmission Type
Engine Type
Engine Size
Engine Cylinder Count
Engine/Motor(s) Description
Manufacturer
Manufacturer URL
Category
Fuel Code
Fuel
Fuel Configuration Name
Electric-Only Range
PHEV Total Range
PHEV Type
Notes
Drivetrain
Charging Rate Level 2 (kW)
Charging Rate DC Fast (kW)
Charging Speed Level 1 (miles added per hour of charging)
Charging Speed Level 2 (miles added per hour of charging)
Charging Speed DC Fast (miles added per hour of charging)
Battery Voltage
Battery Capacity Amp Hours
Battery Capacity kWh
Seating Capacity


In [55]:
vehicles.sample(2)

Vehicle ID  Fuel ID Fuel Configuration ID  Manufacturer ID  Category ID  \
3114         649       49                     5              219           27   
2080       11244       45                     9              347           29   

               Model  Model Year Alternative Fuel Economy City  \
3114      Taurus FFV        1991                            14   
2080  Touareg Hybrid        2014                                 

     Alternative Fuel Economy Highway Alternative Fuel Economy Combined  ...  \
3114                               19                                    ...   
2080                                                                     ...   

     Drivetrain Charging Rate Level 2 (kW) Charging Rate DC Fast (kW)  \
3114                                                                    
2080                                                                    

     Charging Speed Level 1 (miles added per hour of charging)  \
3114                                                             
2080                                                             

     Charging Speed Level 2 (miles added per hour of charging)  \
3114                                                             
2080                                                             

     Charging Speed DC Fast (miles added per hour of charging)  \
3114                                                             
2080                                                             

     Battery Voltage Battery Capacity Amp Hours Battery Capacity kWh  \
3114                                                                   
2080                                                                   

     Seating Capacity  
3114                   
2080                   

[2 rows x 38 columns]

In [56]:
fig = px.histogram(vehicles, x="Fuel Code")
fig.layout["xaxis"]["title"] = "Fuel Type"
fig.layout["yaxis"]["title"] = "Count"
fig

## Dataset USA Alternative Fuels Stations
- Last update 26/10/2022
- Source: https://afdc.energy.gov/data_download
- Columns Explanation: https://afdc.energy.gov/data_download/alt_fuel_stations_format

In [57]:
# Global variables
last_update = "(October 2022)"

In [58]:
# read csv
stations=pd.read_csv("Data/26:10:2022/alt_fuel_stations.csv", keep_default_na=False)
print(f"Number of Columns: {len(stations.columns)} \n")
print("\n".join(stations.columns))
stations["Geocode Status"].sample(2)

Number of Columns: 65 

Fuel Type Code
Station Name
Street Address
Intersection Directions
City
State
ZIP
Plus4
Station Phone
Status Code
Expected Date
Groups With Access Code
Access Days Time
Cards Accepted
BD Blends
NG Fill Type Code
NG PSI
EV Level1 EVSE Num
EV Level2 EVSE Num
EV DC Fast Count
EV Other Info
EV Network
EV Network Web
Geocode Status
Latitude
Longitude
Date Last Confirmed
ID
Updated At
Owner Type Code
Federal Agency ID
Federal Agency Name
Open Date
Hydrogen Status Link
NG Vehicle Class
LPG Primary
E85 Blender Pump
EV Connector Types
Country
Intersection Directions (French)
Access Days Time (French)
BD Blends (French)
Groups With Access Code (French)
Hydrogen Is Retail
Access Code
Access Detail Code
Federal Agency Code
Facility Type
CNG Dispenser Num
CNG On-Site Renewable Source
CNG Total Compression Capacity
CNG Storage Capacity
LNG On-Site Renewable Source
E85 Other Ethanol Blends
EV Pricing
EV Pricing (French)
LPG Nozzle Types
Hydrogen Pressures
Hydrogen Standards
CN

/var/folders/gc/wbs5xnpx3g97_gqgg_y46mgm0000gn/T/ipykernel_55114/2540500635.py:2: DtypeWarning:

Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.



51091    GPS
39604    GPS
Name: Geocode Status, dtype: object

In [59]:
# capitilize all acccess codes
stations["Access Code"] = stations["Access Code"].str.capitalize()

In [60]:
fig = px.pie(stations, names="Access Code")

fig.update_traces(
    textposition= "inside",
    textinfo='percent+label',
)

fig.update_layout(
    height=500, 
    showlegend=False,
    title=go.layout.Title(text="Public and Private Alternative Fuels Stations".title(), x=0.5),
    uniformtext_minsize=12, 
    uniformtext_mode='hide',
)

fig

In [61]:
statusCodes = {
  "E": "Available",
  "T": "Unavailable",
  "P": "Planned",
}

def mapStatusCode(x):
    return statusCodes[x]

stations["Status"] = stations["Status Code"].map(lambda x:mapStatusCode(x))

fig = px.pie(stations, names="Status")

fig.update_traces(
    textposition= "inside",
    textinfo='percent+label',
)

fig.update_layout(
    height=500, 
    showlegend=True,
    uniformtext_minsize=12, 
    uniformtext_mode='hide',
    title=go.layout.Title(text="Aviability Alternative Fuels Stations".title(), x=0.5),
)

fig

From the graph we can tell that the majority of the stations are Avaible, so the dataset as it is can tell almost accuratly what stations are avaible right now.
If we want to accuratly analise the stations avaible right now, we need tho filter the stations with "Status == Available"

In [62]:
# Available Stations
available_stations = stations[stations["Status Code"] == "E"]

In [63]:
# add column year
available_stations["Year"] = available_stations["Open Date"].map(lambda x: x.split("-")[0])
# delete columns with empty year
available_stations = available_stations[available_stations["Year"] != ""]
# convert year to int
available_stations["Year"] = available_stations["Year"].map(lambda x: int(x))
# map year 0022 to 2022
available_stations["Year"] = available_stations["Year"].map(lambda x: 2000 + x if x < 100 else x)

print(available_stations["Year"].unique())

[2010 1994 1996 1997 2016 1988 2014 1998 1991 2001 1987 1989 1986 1995
 2004 1992 2008 2013 2011 1990 2002 1993 1999 2009 2003 2006 1985 2020
 2019 2015 2021 2005 2018 2012 2000 2017 2007 2022 1974 1984 1976 1978]


/var/folders/gc/wbs5xnpx3g97_gqgg_y46mgm0000gn/T/ipykernel_55114/2756868318.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [64]:
# add column state full with state full name

us_state_to_abbrev = {
    "Alabama": "AL",
    "Alaska": "AK",
    "Arizona": "AZ",
    "Arkansas": "AR",
    "California": "CA",
    "Colorado": "CO",
    "Connecticut": "CT",
    "Delaware": "DE",
    "Florida": "FL",
    "Georgia": "GA",
    "Hawaii": "HI",
    "Idaho": "ID",
    "Illinois": "IL",
    "Indiana": "IN",
    "Iowa": "IA",
    "Kansas": "KS",
    "Kentucky": "KY",
    "Louisiana": "LA",
    "Maine": "ME",
    "Maryland": "MD",
    "Massachusetts": "MA",
    "Michigan": "MI",
    "Minnesota": "MN",
    "Mississippi": "MS",
    "Missouri": "MO",
    "Montana": "MT",
    "Nebraska": "NE",
    "Nevada": "NV",
    "New Hampshire": "NH",
    "New Jersey": "NJ",
    "New Mexico": "NM",
    "New York": "NY",
    "North Carolina": "NC",
    "North Dakota": "ND",
    "Ohio": "OH",
    "Oklahoma": "OK",
    "Oregon": "OR",
    "Pennsylvania": "PA",
    "Rhode Island": "RI",
    "South Carolina": "SC",
    "South Dakota": "SD",
    "Tennessee": "TN",
    "Texas": "TX",
    "Utah": "UT",
    "Vermont": "VT",
    "Virginia": "VA",
    "Washington": "WA",
    "West Virginia": "WV",
    "Wisconsin": "WI",
    "Wyoming": "WY",
    "District of Columbia": "DC",
    "American Samoa": "AS",
    "Guam": "GU",
    "Northern Mariana Islands": "MP",
    "Puerto Rico": "PR",
    "United States Minor Outlying Islands": "UM",
    "U.S. Virgin Islands": "VI",
}
    
# invert the dictionary
abbrev_to_us_state = dict(map(reversed, us_state_to_abbrev.items()))

def mapUsaStates(x):
    return abbrev_to_us_state[x.upper()]

# delete rows with not valid state code
available_stations = available_stations.loc[~available_stations["State"].isin(["ON","MX","QC",""])]

# add new column with full state name 
available_stations["State Full"] = available_stations["State"].map(lambda x:mapUsaStates(x))

In [65]:
# add new column with full type fuel name

mapFuelTypeCode = {
  "ELEC": "Electric",
  "E85": "Ethanol",
  "LPG": "Liquefied petroleum gas",
  "CNG": "Compressed natural gas",
  "BD": "Biodisel",
  "LNG": "Liquefied Natural Gas",
  "HY": "Hydrogen"
}

def mapFuel(x):
    return mapFuelTypeCode[x]

available_stations["Fuel Type"] = available_stations.loc[:,"Fuel Type Code"].map(lambda x:mapFuel(x))

In [66]:
# count of stations by year and fuel type
stations_by_year = available_stations.groupby(["Year","Fuel Type"]).size().reset_index(name="Count")
# sort by year
stations_by_year = stations_by_year.sort_values(by=["Year"])
# add column with cumulative sum
stations_by_year["Cumulative"] = stations_by_year.groupby("Fuel Type")["Count"].cumsum()
# add column max year (interger) for each fuel type
stations_by_year["Max Year"] = stations_by_year.groupby("Fuel Type")["Year"].transform(max).astype('int')

# add column max cumulative for each fuel type
stations_by_year["Max Cumulative"] = stations_by_year.groupby("Fuel Type")["Cumulative"].transform(max)
# delete rows with year < 2000
stations_by_year = stations_by_year[stations_by_year["Year"] >= 2000]

# colors for fuel type
colors = {
    "Electric": "#1f77b4",
    "Ethanol": "#ff7f0e",
    "Liquefied petroleum gas": "#2ca02c",
    "Compressed natural gas": "#d62728",
    "Biodisel": "#9467bd",
    "Liquefied Natural Gas": "#8c564b",
    "Hydrogen": "#e377c2"
}

labels = {
    "Electric": "Electric",
    "Ethanol": "Ethanol",
    "Liquefied petroleum gas": "LPG",
    "Compressed natural gas": "CNG",
    "Biodisel": "Biodisel",
    "Liquefied Natural Gas": "LNG",
    "Hydrogen": "Hydrogen"
}

arrowYOffset = {
    "Electric": 0,
    "Ethanol": 0,
    "Liquefied petroleum gas": 0,
    "Compressed natural gas": 0,
    "Biodisel": 10,
    "Liquefied Natural Gas": 30,
    "Hydrogen": 10
}

# line graph of stations by year and fuel type
fig = px.line(
    stations_by_year, 
    x="Year", 
    y="Cumulative", 
    color="Fuel Type", 
    symbol="Fuel Type",
    color_discrete_map=colors,
    )


fig.update_layout(
    title=f"Number of Alternative Fuel Stations by Year {last_update}",
    xaxis_title="Year",
    yaxis_title="Number of Stations"
)

uniqueFuels = stations_by_year[["Fuel Type","Max Year","Max Cumulative"]].drop_duplicates()
annotations = []

for index, row in uniqueFuels.iterrows():
    annotations.append(
            dict(
                x=row["Max Year"],
                y=row["Max Cumulative"],
                ax=30, # arrowhead x position
                ay=-10 + arrowYOffset[row["Fuel Type"]], # arrowhead y position
                xshift=2, # x shift of text and arrowhead
                text=labels[row["Fuel Type"]],
                arrowcolor="black",
                arrowsize=1,
                arrowwidth=1,
                arrowhead=5, # arrowhead type
                xanchor="left",
                yanchor="middle",
                opacity=0.7,
                font=dict(
                    color=colors[row["Fuel Type"]],
                    size=12
                ),
            )
        )

fig.update_layout(
    showlegend=False,
    height=900,
    annotations=annotations
)

fig

In [67]:
fig = px.histogram(available_stations, y="State Full")
fig.layout["xaxis"]["title"] = "State"
fig.layout["yaxis"]["title"] = "Count"
fig.layout.title = "Available Alternative Vehicles Stations per State " + last_update
fig.update_layout(
    yaxis={'categoryorder':'total ascending'},
    height=900
    )
    
fig

#### Data
- States with more available stations are California, New York, Texas, Florida

#### Informations
- Populated states with "warm climates" have more installed stations, 
    - maybe because electric stations in combination with a solar array is more a vaiable solution
    - or maybe becouse this states are more populated or have just more demand for electric vehicle


In [68]:
# pie chart of stations by fuel type

fig = px.pie(available_stations, names="Fuel Type")
fig.layout.title = "Types of Available Alternative Vehicle Stations " + last_update
fig.update_traces(
    textposition= "inside",
    textinfo='percent+label',
)

# annotation labels for hydrogen and liquefied natural gas
#annotations = [
#    dict(
#        x=0,
#        y=0,
#        text="Hydrogen",
#        showarrow=True,
#        font=dict(
#            color=colors["Hydrogen"],
#            size=12
#        ),
#    ),
#    dict(
#        x=0.5,
#        y=0.5,
#        text="Liquefied Natural Gas",
#        showarrow=True,
#        ax=40, # arrowhead x position
#        ay=-10, # arrowhead y position
#        xshift=2, # x shift of text and arrowhead
#        arrowcolor="black",
#        arrowsize=1,
#        arrowwidth=1,
#        arrowhead=5, # arrowhead type
#        xanchor="right",
#        yanchor="top",
#        opacity=0.7,
#        font=dict(
#            color=colors["Liquefied Natural Gas"],
#            size=12
#        ),
#    )
#]

fig.update_layout(
    height=900, 
    showlegend=True, 
    annotations=annotations,
    uniformtext_minsize=12, 
    uniformtext_mode='hide',
)

fig

#### Data
- Most available stations are for electric vehicles 84%
- Available Hydrogen stations compose only the 0.1%

#### Informations
- we can assume with certainty that most popular "alternative" vehicles are electric vehicles
- the same can be said about stations 
- from this date we can say that the future is unlikely to be hydrogen, is likely electic

## So now we analyse electric stations 

In [69]:
# Get only Available Electric Stations
electric_stations = available_stations[available_stations["Fuel Type Code"] == "ELEC"]

fig = px.histogram(electric_stations, y="State Full")
fig.layout["xaxis"]["title"] = "State"
fig.layout["yaxis"]["title"] = "Count"
fig.layout.title = "Electric Vehicles Stations per State " + last_update
fig.update_layout(yaxis={'categoryorder':'total ascending'})
fig

In [70]:
df = electric_stations

#group by Ev Network
df = df.groupby(['EV Network']).size().reset_index(name='counts')
# total number of stations
total = df['counts'].sum()
# add percentage column
df['percentage'] = df['counts'].apply(lambda x: round(x/total*100,2))

# add new row with EV Network = "Other"
mask = (df['percentage'] < 2) | (df['EV Network'] == 'Non-Networked')
others = df[mask]
df = df[~mask]
# concat the new row with the rest of the dataframe
row = pd.DataFrame({'EV Network': 'Others', 'counts': others['counts'].sum(), 'percentage': others['percentage'].sum()}, index=[0])
df = pd.concat([df, row], ignore_index=True)

# pie chart with direct labels
fig = px.pie(
    df, values='counts', 
    names='EV Network', 
    title='Electric Vehicle Stations by Network ' + last_update,
)
fig.update_traces(textposition='inside', textinfo='percent+label')
fig.update_layout(height=900, showlegend=False, title_x=0.5,)
fig

In [76]:
import plotly.graph_objects as go

electric_stations_states = electric_stations[['State', 'State Full']]
electric_stations_states['count'] = electric_stations_states.groupby('State')['State'].transform('count')
electric_stations_states = electric_stations_states.drop_duplicates()

electric_stations_states['text'] = 'State: ' + electric_stations_states['State Full']

fig = go.Figure(data=go.Choropleth(
    locations=electric_stations_states['State'], # Spatial coordinates
    z = electric_stations_states['count'].astype(float), # Data to be color-coded
    locationmode = 'USA-states', # set of locations match entries in `locations`
    colorscale = 'Reds',
    text=electric_stations_states['text'], # hover text
    marker_line_color='black', # line markers between states
    colorbar_title = " Available Electric Stations",
))

fig.update_layout(
    title_text = 'Available Electric Vehicle Stations per State ' + last_update,
    geo_scope='usa', # limite map scope to USA
)

fig.show()


/var/folders/gc/wbs5xnpx3g97_gqgg_y46mgm0000gn/T/ipykernel_55114/3254165688.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



#### Seeing the resulting graph we can tell:
- Mybe there is a correletion with warm climents, with mostly sunny wheather and number of electric stations 